## Train a character-level GPT on some text data

The inputs here are simple text files, which we chop up to individual characters and then train GPT on. So you could say this is a char-transformer instead of a char-rnn. Doesn't quite roll off the tongue as well. In this example we will feed it some Shakespeare, which we'll get it to predict character-level.

In [1]:
from allennlp.data.token_indexers import TokenIndexer, PretrainedTransformerIndexer
from allennlp.data.tokenizers import Token, Tokenizer, PretrainedTransformerTokenizer
import nltk
#nltk.download('punkt')
import numpy as np
from os import listdir
from os.path import join as pathjoin
import torch
import torch.nn as nn
from torch.nn import functional as F
import tqdm

from minGPT.mingpt.model import GPT, GPTConfig
from minGPT.mingpt.trainer import Trainer, TrainerConfig
# make deterministic
from minGPT.mingpt.utils import sample, set_seed
set_seed(42)

In [2]:
DATA_DIR = '/home/mlepekhin/data'
MODELS_DIR = '/home/mlepekhin/models'
transformer_model = 'DeepPavlov/rubert-base-cased'

In [3]:
from allennlp.data import Vocabulary


tokenizer = PretrainedTransformerTokenizer(transformer_model)
indexer = PretrainedTransformerIndexer(transformer_model)
bert_vocab = Vocabulary().from_files(
    pathjoin('/home/mlepekhin/models', 'allennlp_rubert_from_discriminator', 'vocab')
)

In [4]:
indexer.tokens_to_indices(tokenizer.tokenize('присоединились'), bert_vocab)

{'token_ids': [101, 29895, 102],
 'mask': [True, True, True],
 'type_ids': [0, 0, 0]}

In [5]:
bert_token_to_index = bert_vocab.get_token_to_index_vocabulary('tags')
bert_token_to_index['присоединились']

29895

In [6]:
import math
from torch.utils.data import Dataset

def detokenize(tokens):
    return ' '.join([str(x) for x in tokens[1:-1]]).replace(' ##', '')

class BPEDataset(Dataset):
    def __init__(self, data, block_size):
        data_size, vocab_size = len(data), len(bert_token_to_index)
        print('data has %d characters, %d unique.' % (data_size, vocab_size))
        
        self.block_size = block_size
        self.vocab_size = vocab_size
        self.data = data
    
    def __len__(self):
        return len(self.data) - self.block_size

    def __getitem__(self, idx):
        # grab a chunk of (block_size + 1) characters from the data
        chunk = self.data[idx:idx + self.block_size + 1]
        # encode every character to an integer
        dix = [bert_token_to_index[word] for word in chunk]
        """
        arrange data and targets so that the first i elements of x
        will be asked to predict the i-th element of y. Notice that
        the eventual language model will actually make block_size
        individual predictions at the same time based on this data,
        so we are being clever and amortizing the cost of the forward
        pass of the network. So for example if block_size is 4, then
        we could e.g. sample a chunk of text "hello", the integers in
        x will correspond to "hell" and in y will be "ello". This will
        then actually "multitask" 4 separate examples at the same time
        in the language model:
        - given just "h", please predict "e" as next
        - given "he" please predict "l" next
        - given "hel" predict "l" next
        - given "hell" predict "o" next
        
        In addition, because the DataLoader will create batches of examples,
        every forward/backward pass during traning will simultaneously train
        a LOT of predictions, amortizing a lot of computation. In particular,
        for a batched input of integers X (B, T) where B is batch size and
        T is block_size and Y (B, T), the network will during training be
        simultaneously training to make B*T predictions, all at once! Of course,
        at test time we can paralellize across batch B, but unlike during training
        we cannot parallelize across the time dimension T - we have to run
        a forward pass of the network to recover the next single character of the 
        sequence along each batch dimension, and repeatedly always feed in a next
        character to get the next one.
        
        So yes there is a big asymmetry between train/test time of autoregressive
        models. During training we can go B*T at a time with every forward pass,
        but during test time we can only go B at a time, T times, with T forward 
        passes.
        """
        x = torch.tensor(dix[:-1], dtype=torch.long)
        y = torch.tensor(dix[1:], dtype=torch.long)
        return x, y


In [7]:
block_size = 128

In [8]:
def train_gpt_generator(train_text_file, state_dict_file, n_layer=4, n_head=4, n_embd=256,
                        max_epochs=2, batch_size=64):
    text_sentences = nltk.tokenize.sent_tokenize(open(train_text_file, 'r').read())
    tokens = np.concatenate([tokenizer.tokenize(sent) for sent in text_sentences])
    tokens = [str(token) for token in tokens]
    train_dataset = BPEDataset(tokens, block_size) 
    
    mconf = GPTConfig(
        train_dataset.vocab_size, train_dataset.block_size,
        n_layer=n_layer, n_head=n_head, n_embd=n_embd
    )
    model = GPT(mconf)
    tconf = TrainerConfig(
        max_epochs=max_epochs, batch_size=batch_size, learning_rate=6e-4,
        lr_decay=True, warmup_tokens=batch_size*20, final_tokens=2*len(train_dataset)*block_size,
    )
    trainer = Trainer(model, train_dataset, None, tconf)
    trainer.train()
    torch.save(model.state_dict(), state_dict_file)

In [9]:
GENRE_DATA_DIR = '/home/mlepekhin/data/train_genre'
GPT_MODELS_DIR = '/home/mlepekhin/models/mini_gpt_bpe_tuned/'
LANG = 'ru'

In [10]:
#train_gpt_generator(
#        pathjoin(GENRE_DATA_DIR, LANG, 'A1.txt'),
#        pathjoin(GPT_MODELS_DIR, LANG, 'A1')
#)

In [11]:
for train_text_file in tqdm.tqdm(listdir(pathjoin(GENRE_DATA_DIR, LANG))):
    label = train_text_file[:-4]
    train_gpt_generator(
        pathjoin(GENRE_DATA_DIR, LANG, train_text_file),
        pathjoin(GPT_MODELS_DIR, LANG, label)
    )

  0%|          | 0/10 [00:00<?, ?it/s]

data has 199175 characters, 119547 unique.



  0%|          | 0/3111 [00:00<?, ?it/s]/home/mlepekhin/anaconda3/envs/mlepekhin_research/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '

epoch 1 iter 0: train loss 11.73162. lr 6.000000e-04:   0%|          | 0/3111 [00:02<?, ?it/s]
epoch 1 iter 0: train loss 11.73162. lr 6.000000e-04:   0%|          | 1/3111 [00:02<2:26:22,  2.82s/it]
epoch 1 iter 1: train loss 11.26046. lr 5.999999e-04:   0%|          | 1/3111 [00:03<2:26:22,  2.82s/it]
epoch 1 iter 1: train loss 11.26046. lr 5.999999e-04:   0%|          | 2/3111 [00:03<1:48:01,  2.08s/it]
epoch 1 iter 2: train loss 11.01675. lr 5.999997e-04:   0%|          | 2/3111 [00:03<1:48:01,  2.08s/it]
epoch 1 iter 2: train loss 11.01675. lr 5.999997e-04:   0%|          | 3/3111 [00:03<1:21:07,  1.57s/it]
epoch 1 iter 3: train loss

epoch 1 iter 36: train loss 6.79981. lr 5.999481e-04:   1%|          | 37/3111 [00:15<18:16,  2.80it/s]
epoch 1 iter 37: train loss 6.82705. lr 5.999452e-04:   1%|          | 37/3111 [00:15<18:16,  2.80it/s]
epoch 1 iter 37: train loss 6.82705. lr 5.999452e-04:   1%|          | 38/3111 [00:15<18:15,  2.81it/s]
epoch 1 iter 38: train loss 6.75523. lr 5.999423e-04:   1%|          | 38/3111 [00:16<18:15,  2.81it/s]
epoch 1 iter 38: train loss 6.75523. lr 5.999423e-04:   1%|▏         | 39/3111 [00:16<18:14,  2.81it/s]
epoch 1 iter 39: train loss 6.71545. lr 5.999393e-04:   1%|▏         | 39/3111 [00:16<18:14,  2.81it/s]
epoch 1 iter 39: train loss 6.71545. lr 5.999393e-04:   1%|▏         | 40/3111 [00:16<18:13,  2.81it/s]
epoch 1 iter 40: train loss 6.72391. lr 5.999362e-04:   1%|▏         | 40/3111 [00:17<18:13,  2.81it/s]
epoch 1 iter 40: train loss 6.72391. lr 5.999362e-04:   1%|▏         | 41/3111 [00:17<18:12,  2.81it/s]
epoch 1 iter 41: train loss 6.81989. lr 5.999330e-04:   1%|▏    

epoch 1 iter 74: train loss 6.25344. lr 5.997857e-04:   2%|▏         | 75/3111 [00:29<17:59,  2.81it/s]
epoch 1 iter 75: train loss 6.36253. lr 5.997799e-04:   2%|▏         | 75/3111 [00:29<17:59,  2.81it/s]
epoch 1 iter 75: train loss 6.36253. lr 5.997799e-04:   2%|▏         | 76/3111 [00:29<17:59,  2.81it/s]
epoch 1 iter 76: train loss 5.91137. lr 5.997741e-04:   2%|▏         | 76/3111 [00:29<17:59,  2.81it/s]
epoch 1 iter 76: train loss 5.91137. lr 5.997741e-04:   2%|▏         | 77/3111 [00:29<17:59,  2.81it/s]
epoch 1 iter 77: train loss 6.21149. lr 5.997682e-04:   2%|▏         | 77/3111 [00:30<17:59,  2.81it/s]
epoch 1 iter 77: train loss 6.21149. lr 5.997682e-04:   3%|▎         | 78/3111 [00:30<17:58,  2.81it/s]
epoch 1 iter 78: train loss 6.18482. lr 5.997622e-04:   3%|▎         | 78/3111 [00:30<17:58,  2.81it/s]
epoch 1 iter 78: train loss 6.18482. lr 5.997622e-04:   3%|▎         | 79/3111 [00:30<17:58,  2.81it/s]
epoch 1 iter 79: train loss 6.11024. lr 5.997561e-04:   3%|▎    

...

epoch 2 iter 3233: train loss 0.15369. lr 6.000000e-05:  95%|█████████▌| 3234/3397 [19:55<00:59,  2.72it/s]
epoch 2 iter 3234: train loss 0.14953. lr 6.000000e-05:  95%|█████████▌| 3234/3397 [19:55<00:59,  2.72it/s]
epoch 2 iter 3234: train loss 0.14953. lr 6.000000e-05:  95%|█████████▌| 3235/3397 [19:55<00:59,  2.72it/s]
epoch 2 iter 3235: train loss 0.15018. lr 6.000000e-05:  95%|█████████▌| 3235/3397 [19:56<00:59,  2.72it/s]
epoch 2 iter 3235: train loss 0.15018. lr 6.000000e-05:  95%|█████████▌| 3236/3397 [19:56<00:59,  2.71it/s]
epoch 2 iter 3236: train loss 0.14158. lr 6.000000e-05:  95%|█████████▌| 3236/3397 [19:56<00:59,  2.71it/s]
epoch 2 iter 3236: train loss 0.14158. lr 6.000000e-05:  95%|█████████▌| 3237/3397 [19:56<00:58,  2.71it/s]
epoch 2 iter 3237: train loss 0.13085. lr 6.000000e-05:  95%|█████████▌| 3237/3397 [19:56<00:58,  2.71it/s]
epoch 2 iter 3237: train loss 0.13085. lr 6.000000e-05:  95%|█████████▌| 3238/3397 [19:56<00:58,  2.71it/s]
epoch 2 iter 3238: train los

epoch 2 iter 3270: train loss 0.14341. lr 6.000000e-05:  96%|█████████▋| 3270/3397 [20:09<00:46,  2.71it/s]
epoch 2 iter 3270: train loss 0.14341. lr 6.000000e-05:  96%|█████████▋| 3271/3397 [20:09<00:46,  2.71it/s]
epoch 2 iter 3271: train loss 0.14679. lr 6.000000e-05:  96%|█████████▋| 3271/3397 [20:09<00:46,  2.71it/s]
epoch 2 iter 3271: train loss 0.14679. lr 6.000000e-05:  96%|█████████▋| 3272/3397 [20:09<00:46,  2.72it/s]
epoch 2 iter 3272: train loss 0.15316. lr 6.000000e-05:  96%|█████████▋| 3272/3397 [20:09<00:46,  2.72it/s]
epoch 2 iter 3272: train loss 0.15316. lr 6.000000e-05:  96%|█████████▋| 3273/3397 [20:09<00:45,  2.71it/s]
epoch 2 iter 3273: train loss 0.13134. lr 6.000000e-05:  96%|█████████▋| 3273/3397 [20:10<00:45,  2.71it/s]
epoch 2 iter 3273: train loss 0.13134. lr 6.000000e-05:  96%|█████████▋| 3274/3397 [20:10<00:45,  2.72it/s]
epoch 2 iter 3274: train loss 0.13986. lr 6.000000e-05:  96%|█████████▋| 3274/3397 [20:10<00:45,  2.72it/s]
epoch 2 iter 3274: train los

epoch 2 iter 3306: train loss 0.14033. lr 6.000000e-05:  97%|█████████▋| 3307/3397 [20:22<00:33,  2.70it/s]
epoch 2 iter 3307: train loss 0.13036. lr 6.000000e-05:  97%|█████████▋| 3307/3397 [20:22<00:33,  2.70it/s]
epoch 2 iter 3307: train loss 0.13036. lr 6.000000e-05:  97%|█████████▋| 3308/3397 [20:22<00:32,  2.71it/s]
epoch 2 iter 3308: train loss 0.15005. lr 6.000000e-05:  97%|█████████▋| 3308/3397 [20:23<00:32,  2.71it/s]
epoch 2 iter 3308: train loss 0.15005. lr 6.000000e-05:  97%|█████████▋| 3309/3397 [20:23<00:32,  2.72it/s]
epoch 2 iter 3309: train loss 0.14595. lr 6.000000e-05:  97%|█████████▋| 3309/3397 [20:23<00:32,  2.72it/s]
epoch 2 iter 3309: train loss 0.14595. lr 6.000000e-05:  97%|█████████▋| 3310/3397 [20:23<00:32,  2.72it/s]
epoch 2 iter 3310: train loss 0.15426. lr 6.000000e-05:  97%|█████████▋| 3310/3397 [20:23<00:32,  2.72it/s]
epoch 2 iter 3310: train loss 0.15426. lr 6.000000e-05:  97%|█████████▋| 3311/3397 [20:23<00:31,  2.71it/s]
epoch 2 iter 3311: train los

epoch 2 iter 3343: train loss 0.14778. lr 6.000000e-05:  98%|█████████▊| 3343/3397 [20:35<00:19,  2.71it/s]
epoch 2 iter 3343: train loss 0.14778. lr 6.000000e-05:  98%|█████████▊| 3344/3397 [20:35<00:19,  2.72it/s]
epoch 2 iter 3344: train loss 0.14134. lr 6.000000e-05:  98%|█████████▊| 3344/3397 [20:36<00:19,  2.72it/s]
epoch 2 iter 3344: train loss 0.14134. lr 6.000000e-05:  98%|█████████▊| 3345/3397 [20:36<00:19,  2.72it/s]
epoch 2 iter 3345: train loss 0.13387. lr 6.000000e-05:  98%|█████████▊| 3345/3397 [20:36<00:19,  2.72it/s]
epoch 2 iter 3345: train loss 0.13387. lr 6.000000e-05:  98%|█████████▊| 3346/3397 [20:36<00:18,  2.71it/s]
epoch 2 iter 3346: train loss 0.14708. lr 6.000000e-05:  98%|█████████▊| 3346/3397 [20:37<00:18,  2.71it/s]
epoch 2 iter 3346: train loss 0.14708. lr 6.000000e-05:  99%|█████████▊| 3347/3397 [20:37<00:18,  2.72it/s]
epoch 2 iter 3347: train loss 0.13840. lr 6.000000e-05:  99%|█████████▊| 3347/3397 [20:37<00:18,  2.72it/s]
epoch 2 iter 3347: train los

epoch 2 iter 3379: train loss 0.14560. lr 6.000000e-05:  99%|█████████▉| 3380/3397 [20:49<00:06,  2.72it/s]
epoch 2 iter 3380: train loss 0.13876. lr 6.000000e-05:  99%|█████████▉| 3380/3397 [20:49<00:06,  2.72it/s]
epoch 2 iter 3380: train loss 0.13876. lr 6.000000e-05: 100%|█████████▉| 3381/3397 [20:49<00:05,  2.71it/s]
epoch 2 iter 3381: train loss 0.14916. lr 6.000000e-05: 100%|█████████▉| 3381/3397 [20:49<00:05,  2.71it/s]
epoch 2 iter 3381: train loss 0.14916. lr 6.000000e-05: 100%|█████████▉| 3382/3397 [20:49<00:05,  2.71it/s]
epoch 2 iter 3382: train loss 0.14151. lr 6.000000e-05: 100%|█████████▉| 3382/3397 [20:50<00:05,  2.71it/s]
epoch 2 iter 3382: train loss 0.14151. lr 6.000000e-05: 100%|█████████▉| 3383/3397 [20:50<00:05,  2.71it/s]
epoch 2 iter 3383: train loss 0.14498. lr 6.000000e-05: 100%|█████████▉| 3383/3397 [20:50<00:05,  2.71it/s]
epoch 2 iter 3383: train loss 0.14498. lr 6.000000e-05: 100%|█████████▉| 3384/3397 [20:50<00:04,  2.72it/s]
epoch 2 iter 3384: train los